In [1]:
!pip install xmltodict

In [2]:
import urllib
import xmltodict
import pandas as pd

xml_url = 'https://data.bmkg.go.id/DataMKG/MEWS/DigitalForecast/DigitalForecast-Indonesia.xml'
xml_data = urllib.request.urlopen(xml_url)
dataset = xmltodict.parse(xml_data)
dataset

OrderedDict([('data',
              OrderedDict([('@source', 'meteofactory'),
                           ('@productioncenter', 'NC Jakarta'),
                           ('forecast',
                            OrderedDict([('@domain', 'local'),
                                         ('issue',
                                          OrderedDict([('timestamp',
                                                        '20210630034316'),
                                                       ('year', '2021'),
                                                       ('month', '06'),
                                                       ('day', '30'),
                                                       ('hour', '03'),
                                                       ('minute', '43'),
                                                       ('second', '16')])),
                                         ('area',
                                          [OrderedDict([('@id', '501397'),


In [3]:
from datetime import datetime

def convert_timerange(timerange):
  datetimeobj = datetime.strptime(timerange, '%Y%m%d%H%M')
  return datetimeobj.strftime('%d %B %Y %H:%M')

In [4]:
areas = pd.DataFrame(dataset['data']['forecast']['area'])
latitude = areas['@latitude']
longitude = areas['@longitude']
city = areas['@description']
weather = {}
for i,area in areas['parameter'].iteritems():
  weathers = area[6]
  for w in weathers['timerange']:
    timerange = w['@datetime']
    timerange = convert_timerange(timerange)
    value = w['value']['#text']
    if timerange not in weather:
      weather[timerange] = {}
    if city[i] not in weather[timerange]:
      weather[timerange][city[i]] = {}
    weather[timerange][city[i]] = value

In [5]:
data = {'City': city,
        'Latitude': latitude,
        'Longitude': longitude}
pd.DataFrame(data)

City      Latitude   Longitude
0       Banda Aceh       5.54491    95.34312
1         Denpasar     -8.643480  115.224609
2           Serang  -6.133333334    106.1667
3         Bengkulu     -3.794373  102.304688
4       Yogyakarta      -7.80279   110.37625
5    Jakarta Pusat     -6.176396  106.826591
6        Gorontalo       0.53175   123.08807
7            Jambi         -1.61      103.59
8          Bandung      -6.90992   107.64691
9         Semarang     -6.959144  110.438690
10        Surabaya      -7.27981   112.71109
11       Pontianak      -0.08902   109.35144
12     Banjarmasin      -3.32828   114.57315
13    Palangkaraya         -2.21      113.92
14       Samarinda      -0.43018   117.17432
15         Tarakan      3.329128  117.571049
16  Pangkal Pinang      -2.19216   106.12806
17  Tanjung Pinang      0.906334  104.562378
18  Bandar Lampung      -5.42396   105.25113
19           Ambon      -3.67265   128.23381
20         Ternate      0.833215  127.365532
21         Mataram      -8.58142   116.11737
22          Kupang     -10.22498   123.60374
23        Jayapura     -2.556219  140.703278
24       Manokwari  -0.900000002   134.00001
25       Pekanbaru       0.55742   101.46218
26          Mamuju  -2.683333335    118.8333
27        Makassar     -5.121379  119.418983
28         Kendari        -3.966       122.6
29          Manado       1.50213   124.85236
30          Padang         -0.88       100.4
31       Palembang     -2.978699  104.751892
32           Medan       3.66681    98.67123

In [6]:
pd.DataFrame(weather)

30 June 2021 00:00  ... 02 July 2021 18:00
Banda Aceh                      1  ...                  3
Denpasar                        1  ...                  0
Serang                         60  ...                  4
Bengkulu                        3  ...                 45
Yogyakarta                      1  ...                  1
Jakarta Pusat                   3  ...                  0
Gorontalo                       1  ...                  3
Jambi                           3  ...                 10
Bandung                         1  ...                  3
Semarang                        3  ...                  1
Surabaya                        3  ...                  0
Pontianak                       1  ...                  1
Banjarmasin                     1  ...                 95
Palangkaraya                    3  ...                  3
Samarinda                      60  ...                 45
Tarakan                         3  ...                  3
Pangkal Pinang                  3  ...                  3
Tanjung Pinang                  3  ...                  3
Bandar Lampung                 60  ...                  1
Ambon                           3  ...                 60
Ternate                         1  ...                 60
Mataram                         1  ...                  1
Kupang                          1  ...                  1
Jayapura                        3  ...                  3
Manokwari                       1  ...                  1
Pekanbaru                      45  ...                  3
Mamuju                          3  ...                  3
Makassar                       60  ...                  3
Kendari                        60  ...                 60
Manado                          1  ...                  3
Padang                          4  ...                  3
Palembang                       3  ...                  1
Medan                           1  ...                  3

[33 rows x 12 columns]

In [7]:
kode_cuaca = {
	'0':'Cerah',
	'1':'Cerah Berawan',
	'2':'Cerah Berawan',
	'3':'Berawan',
	'4':'Berawan Tebal',
	'5':'Udara Kabur',
	'10':'Asap',
	'45':'Kabut',
	'60':'Hujan Ringan',
	'61':'Hujan Sedang',
	'63':'Hujan Lebat',
	'80':'Hujan Lokal',
	'95':'Hujan Petir',
	'97':'Hujan Petir',
}

In [8]:
weather_df = pd.DataFrame(weather)
weather_df.replace(kode_cuaca)

30 June 2021 00:00  ... 02 July 2021 18:00
Banda Aceh          Cerah Berawan  ...            Berawan
Denpasar            Cerah Berawan  ...              Cerah
Serang               Hujan Ringan  ...      Berawan Tebal
Bengkulu                  Berawan  ...              Kabut
Yogyakarta          Cerah Berawan  ...      Cerah Berawan
Jakarta Pusat             Berawan  ...              Cerah
Gorontalo           Cerah Berawan  ...            Berawan
Jambi                     Berawan  ...               Asap
Bandung             Cerah Berawan  ...            Berawan
Semarang                  Berawan  ...      Cerah Berawan
Surabaya                  Berawan  ...              Cerah
Pontianak           Cerah Berawan  ...      Cerah Berawan
Banjarmasin         Cerah Berawan  ...        Hujan Petir
Palangkaraya              Berawan  ...            Berawan
Samarinda            Hujan Ringan  ...              Kabut
Tarakan                   Berawan  ...            Berawan
Pangkal Pinang            Berawan  ...            Berawan
Tanjung Pinang            Berawan  ...            Berawan
Bandar Lampung       Hujan Ringan  ...      Cerah Berawan
Ambon                     Berawan  ...       Hujan Ringan
Ternate             Cerah Berawan  ...       Hujan Ringan
Mataram             Cerah Berawan  ...      Cerah Berawan
Kupang              Cerah Berawan  ...      Cerah Berawan
Jayapura                  Berawan  ...            Berawan
Manokwari           Cerah Berawan  ...      Cerah Berawan
Pekanbaru                   Kabut  ...            Berawan
Mamuju                    Berawan  ...            Berawan
Makassar             Hujan Ringan  ...            Berawan
Kendari              Hujan Ringan  ...       Hujan Ringan
Manado              Cerah Berawan  ...            Berawan
Padang              Berawan Tebal  ...            Berawan
Palembang                 Berawan  ...      Cerah Berawan
Medan               Cerah Berawan  ...            Berawan

[33 rows x 12 columns]